In [1]:
import torch
print(torch.cuda.is_available())

True


In [2]:
import pandas as pd

# Load the scp_statements.csv file
scp_statements_path = r".\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\scp_statements.csv"
scp_statements = pd.read_csv(scp_statements_path)

# List of relevant descriptions for Sinus, AfIB, and Heart Block
sinus_descriptions = ['sinus rhythm', 'normal functioning artificial pacemaker', 'normal ECG']
afib_descriptions = ['atrial fibrillation', 'atrial flutter']
heart_block_descriptions = [
    'AV block', 'first degree AV block', 'second degree AV block', 'third degree AV block', 
    'left bundle branch block', 'right bundle branch block', 'incomplete left bundle branch block', 
    'incomplete right bundle branch block', 'left anterior fascicular block', 'right posterior fascicular block'
]

# Filter for Sinus (normal) based on descriptions
filtered_by_sinus = scp_statements[scp_statements['description'].str.contains('|'.join(sinus_descriptions), case=False, na=False)]
filtered_by_sinus['group'] = 'Sinus'

# Filter for AfIB based on descriptions
filtered_by_afib = scp_statements[scp_statements['description'].str.contains('|'.join(afib_descriptions), case=False, na=False)]
filtered_by_afib['group'] = 'AFib'

# Filter for Heart Block based on descriptions
filtered_by_heart_block = scp_statements[scp_statements['description'].str.contains('|'.join(heart_block_descriptions), case=False, na=False)]
filtered_by_heart_block['group'] = 'Heart Block'

# Combine all the filtered data into one DataFrame
combined_filtered_df = pd.concat([filtered_by_sinus, filtered_by_afib, filtered_by_heart_block]).drop_duplicates()

# Display the resulting DataFrame
print("Combined filtered DataFrame with appropriate groups:")
print(combined_filtered_df[['diagnostic_class', 'description', 'group', 'scp_code']])


Combined filtered DataFrame with appropriate groups:
   diagnostic_class                              description        group  \
4              NORM                               normal ECG        Sinus   
59              NaN                             sinus rhythm        Sinus   
64              NaN  normal functioning artificial pacemaker        Sinus   
60              NaN                      atrial fibrillation         AFib   
67              NaN                           atrial flutter         AFib   
8                CD           left anterior fascicular block  Heart Block   
10               CD     incomplete right bundle branch block  Heart Block   
11               CD                    first degree AV block  Heart Block   
14               CD       complete right bundle branch block  Heart Block   
15               CD        complete left bundle branch block  Heart Block   
33               CD      incomplete left bundle branch block  Heart Block   
41               CD    

C:\Users\Vinh\AppData\Local\Temp\ipykernel_46324\531268411.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_by_sinus['group'] = 'Sinus'
C:\Users\Vinh\AppData\Local\Temp\ipykernel_46324\531268411.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_by_afib['group'] = 'AFib'
C:\Users\Vinh\AppData\Local\Temp\ipykernel_46324\531268411.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

S

In [3]:
import pandas as pd

valid_scp_codes = combined_filtered_df['scp_code'].dropna().unique()
valid_scp_codes

array(['NORM', 'SR', 'PACE', 'AFIB', 'AFLT', 'LAFB', 'IRBBB', '1AVB',
       'CRBBB', 'CLBBB', 'ILBBB', '3AVB', '2AVB'], dtype=object)

In [4]:
import ast

ptbxl_df = pd.read_csv('.\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptbxl_database.csv')

def get_highest_scp_code(scp_dict):
    scp_dict = ast.literal_eval(scp_dict)
    return max(scp_dict, key=scp_dict.get)

ptbxl_df['highest_scp_code'] = ptbxl_df['scp_codes'].apply(get_highest_scp_code)
ptbxl_df.head()

ecg_id  patient_id   age  sex  height  weight  nurse  site     device  \
0       1     15709.0  56.0    1     NaN    63.0    2.0   0.0  CS-12   E   
1       2     13243.0  19.0    0     NaN    70.0    2.0   0.0  CS-12   E   
2       3     20372.0  37.0    1     NaN    69.0    2.0   0.0  CS-12   E   
3       4     17014.0  24.0    0     NaN    82.0    2.0   0.0  CS-12   E   
4       5     17448.0  19.0    1     NaN    70.0    2.0   0.0  CS-12   E   

        recording_date  ...  baseline_drift static_noise burst_noise  \
0  1984-11-09 09:17:34  ...             NaN    , I-V1,           NaN   
1  1984-11-14 12:55:37  ...             NaN          NaN         NaN   
2  1984-11-15 12:49:10  ...             NaN          NaN         NaN   
3  1984-11-15 13:44:57  ...    , II,III,AVF          NaN         NaN   
4  1984-11-17 10:43:15  ...   , III,AVR,AVF          NaN         NaN   

  electrodes_problems extra_beats  pacemaker  strat_fold  \
0                 NaN         NaN        NaN           3   
1                 NaN         NaN        NaN           2   
2                 NaN         NaN        NaN           5   
3                 NaN         NaN        NaN           3   
4                 NaN         NaN        NaN           4   

                 filename_lr                filename_hr highest_scp_code  
0  records100/00000/00001_lr  records500/00000/00001_hr             NORM  
1  records100/00000/00002_lr  records500/00000/00002_hr             NORM  
2  records100/00000/00003_lr  records500/00000/00003_hr             NORM  
3  records100/00000/00004_lr  records500/00000/00004_hr             NORM  
4  records100/00000/00005_lr  records500/00000/00005_hr             NORM  

[5 rows x 29 columns]

In [5]:
filtered_ptbxl_df = ptbxl_df[ptbxl_df['highest_scp_code'].isin(valid_scp_codes)]
filtered_ptbxl_df

ecg_id  patient_id    age  sex  height  weight  nurse  site  \
0           1     15709.0   56.0    1     NaN    63.0    2.0   0.0   
1           2     13243.0   19.0    0     NaN    70.0    2.0   0.0   
2           3     20372.0   37.0    1     NaN    69.0    2.0   0.0   
3           4     17014.0   24.0    0     NaN    82.0    2.0   0.0   
4           5     17448.0   19.0    1     NaN    70.0    2.0   0.0   
...       ...         ...    ...  ...     ...     ...    ...   ...   
21792   21831     11905.0   55.0    1     NaN     NaN    1.0   2.0   
21793   21832      7954.0   63.0    0     NaN     NaN    1.0   2.0   
21795   21834     20703.0  300.0    0     NaN     NaN    1.0   2.0   
21797   21836      8873.0   64.0    1     NaN     NaN    1.0   2.0   
21798   21837     11744.0   68.0    0     NaN     NaN    1.0   2.0   

           device       recording_date  ...  baseline_drift static_noise  \
0       CS-12   E  1984-11-09 09:17:34  ...             NaN    , I-V1,     
1       CS-12   E  1984-11-14 12:55:37  ...             NaN          NaN   
2       CS-12   E  1984-11-15 12:49:10  ...             NaN          NaN   
3       CS-12   E  1984-11-15 13:44:57  ...    , II,III,AVF          NaN   
4       CS-12   E  1984-11-17 10:43:15  ...   , III,AVR,AVF          NaN   
...           ...                  ...  ...             ...          ...   
21792  AT-60    3  2001-05-28 12:49:25  ...             NaN          NaN   
21793  AT-60    3  2001-05-30 14:14:25  ...             NaN          NaN   
21795  AT-60    3  2001-06-05 11:33:39  ...             NaN          NaN   
21797  AT-60    3  2001-06-09 18:21:49  ...             NaN          NaN   
21798  AT-60    3  2001-06-11 16:43:01  ...             NaN   , I-AVL,     

      burst_noise electrodes_problems extra_beats  pacemaker  strat_fold  \
0             NaN                 NaN         NaN        NaN           3   
1             NaN                 NaN         NaN        NaN           2   
2             NaN                 NaN         NaN        NaN           5   
3             NaN                 NaN         NaN        NaN           3   
4             NaN                 NaN         NaN        NaN           4   
...           ...                 ...         ...        ...         ...   
21792         NaN                 NaN         NaN        NaN           9   
21793         NaN                 NaN         NaN        NaN           7   
21795         NaN                 NaN         NaN        NaN           4   
21797         NaN                 NaN        SVES        NaN           8   
21798         NaN                 NaN         NaN        NaN           9   

                     filename_lr                filename_hr highest_scp_code  
0      records100/00000/00001_lr  records500/00000/00001_hr             NORM  
1      records100/00000/00002_lr  records500/00000/00002_hr             NORM  
2      records100/00000/00003_lr  records500/00000/00003_hr             NORM  
3      records100/00000/00004_lr  records500/00000/00004_hr             NORM  
4      records100/00000/00005_lr  records500/00000/00005_hr             NORM  
...                          ...                        ...              ...  
21792  records100/21000/21831_lr  records500/21000/21831_hr             NORM  
21793  records100/21000/21832_lr  records500/21000/21832_hr             LAFB  
21795  records100/21000/21834_lr  records500/21000/21834_hr             NORM  
21797  records100/21000/21836_lr  records500/21000/21836_hr             NORM  
21798  records100/21000/21837_lr  records500/21000/21837_hr             NORM  

[12411 rows x 29 columns]

In [6]:
import os
import wfdb
import re

mit_bih_dir = "C:\Vinh\CSSALT\CSSALT-waveform-classify-model\mit-bih-malignant-ventricular-ectopy-database-1.0.0\mit-bih-malignant-ventricular-ectopy-database-1.0.0"

records = sorted(set(f.split('.')[0] for f in os.listdir(mit_bih_dir) if f.endswith('.atr')))

data = []
for record in records:
    record_path = os.path.join(record) 

    annotation = wfdb.rdann(os.path.join(mit_bih_dir, record), 'atr')
    label = annotation.aux_note[0] if annotation.aux_note else "UNKNOWN"  # Get the first label or use default
    
    label = re.sub(r'[()]', '', label)
    
    data.append({'Record': record_path, 'Label': label})

df = pd.DataFrame(data)
df

Record   Label
0     418      N 
1     419      N 
2     420      N 
3     421      N 
4     422      N 
5     423      N 
6     424      N 
7     425      N 
8     426      N 
9     427      N 
10    428     BI 
11    429     BI 
12    430     BI 
13    602     PM 
14    605  NOISE 
15    607    NOD 
16    609   AFIB 
17    610      N 
18    611   SVTA 
19    612      N 
20    614      B 
21    615   AFIB 

In [ ]:
import os
import wfdb
import matplotlib.pyplot as plt
from tqdm import tqdm

# Define the root directory of the dataset
root_path = r"C:\Vinh\CSSALT\CSSALT-waveform-classify-model\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3"

def load_ecg_signal(path):
    try:
        record = wfdb.rdrecord(path)
        return record.p_signal
    except Exception as e:
        print(f"Error loading signal from {path}: {e}")
        return None

def save_ecg_plot(signal, save_path):
    plt.figure(figsize=(10, 4))
    plt.plot(signal)
    plt.title("ECG Signal")
    plt.xlabel("Time")
    plt.ylabel("Amplitude")
    plt.grid(True)
    plt.tight_layout()
    plt.savefig(save_path)
    plt.close()

output_dir = "ecg_images"
os.makedirs(output_dir, exist_ok=True)
print(f"Saving ECG images to: {output_dir}")

for row in tqdm(filtered_ptbxl_df.itertuples(), total=len(filtered_ptbxl_df), desc="Processing ECG signals"):
    ecg_path = os.path.join(root_path, row.filename_lr)  

    print(f"Loading ECG from: {ecg_path}")

    signal = load_ecg_signal(ecg_path)
    if signal is None or signal.shape[1] <= 0:
        print(f"Skipping {row.filename_lr} due to invalid signal")
        continue

    try:
        lead_signal = signal[:, 0]  # Use lead 0
        save_path = os.path.join(output_dir, f"{os.path.basename(row.filename_lr)}.png")
        save_ecg_plot(lead_signal, save_path)
    except Exception as e:
        print(f"Error saving plot for {row.filename_lr}: {e}")



Saving ECG images to: ecg_images


Processing ECG signals:   0%|                                                                                                    | 0/12411 [00:00<?, ?it/s]

Loading ECG from: C:\Vinh\CSSALT\CSSALT-waveform-classify-model\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\records100/00000/00001_lr


Processing ECG signals:   0%|                                                                                          | 1/12411 [00:00<2:24:58,  1.43it/s]

Loading ECG from: C:\Vinh\CSSALT\CSSALT-waveform-classify-model\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\records100/00000/00002_lr


...

Processing ECG signals:  90%|█████████████████████████████████████████████████████████████████████████████▌        | 11197/12411 [1:08:35<07:14,  2.79it/s]

Loading ECG from: C:\Vinh\CSSALT\CSSALT-waveform-classify-model\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\records100/19000/19313_lr


Processing ECG signals:  90%|█████████████████████████████████████████████████████████████████████████████▌        | 11198/12411 [1:08:36<07:08,  2.83it/s]

Loading ECG from: C:\Vinh\CSSALT\CSSALT-waveform-classify-model\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\records100/19000/19314_lr


Processing ECG signals:  90%|█████████████████████████████████████████████████████████████████████████████▌        | 11199/12411 [1:08:36<06:57,  2.90it/s]

In [26]:
from jupyter_server import serverapp
serverapp.ServerApp.iopub_data_rate_limit = 10000000  # Increase limit

In [30]:
import wfdb

# Define the full path to the record (without extension)
record_path = 'C:\Vinh\CSSALT\CSSALT-waveform-classify-model\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3/records100/06000/06842_lr'  # Adjust path as necessary

try:
    # Read the record (signal and metadata)
    record = wfdb.rdrecord(record_path)

    # Print the signal data and metadata to verify
    print(record.p_signal)  # Signal data
    print(record.__dict__)  # Metadata
except Exception as e:
    print(f"Error loading record: {e}")


[[ 0.018 -0.001 -0.019 ...  0.03  -0.015  0.   ]
 [ 0.014 -0.006 -0.02  ...  0.03  -0.016 -0.003]
 [ 0.022  0.002 -0.02  ...  0.027 -0.02  -0.009]
 ...
 [-0.035  0.038  0.073 ...  0.066 -0.013 -0.071]
 [-0.044  0.024  0.067 ...  0.082 -0.066 -0.082]
 [-0.058  0.016  0.074 ...  0.097 -0.246 -0.031]]
{'record_name': '06842_lr', 'n_sig': 12, 'fs': 100, 'counter_freq': None, 'base_counter': None, 'sig_len': 1000, 'base_time': None, 'base_date': None, 'comments': [], 'sig_name': ['I', 'II', 'III', 'AVR', 'AVL', 'AVF', 'V1', 'V2', 'V3', 'V4', 'V5', 'V6'], 'p_signal': array([[ 0.018, -0.001, -0.019, ...,  0.03 , -0.015,  0.   ],
       [ 0.014, -0.006, -0.02 , ...,  0.03 , -0.016, -0.003],
       [ 0.022,  0.002, -0.02 , ...,  0.027, -0.02 , -0.009],
       ...,
       [-0.035,  0.038,  0.073, ...,  0.066, -0.013, -0.071],
       [-0.044,  0.024,  0.067, ...,  0.082, -0.066, -0.082],
       [-0.058,  0.016,  0.074, ...,  0.097, -0.246, -0.031]]), 'd_signal': None, 'e_p_signal': None, 'e_d_sig